In [ ]:
import os
import re
import sys
import time
import json
import requests
import cloudpickle as pickle
from datetime import timedelta

#  ================= DETECT ENV =================
def detect_environment():
    environments = {
        'COLAB_GPU': ('Google Colab', "/content"),
        'KAGGLE_URL_BASE': ('Kaggle', "/kaggle/working/content"),
        'SAGEMAKER_INTERNAL_IMAGE_URI': ('SageMaker Studio Lab', "/home/studio-lab-user/content")
    }

    for env_var, (environment, path) in environments.items():
        if env_var in os.environ:
            return environment, path

    sys.exit("\033[31mError: an unsupported runtime environment was detected.\n\033[34mSupported environments:\033[0m Google Colab, Kaggle, Sagemaker Studio Lab")

env, root_path = detect_environment()
webui_path = f"{root_path}/sdw"
#  ----------------------------------------------

def load_settings():
    SETTINGS_FILE = f'{root_path}/settings.json'
    if os.path.exists(SETTINGS_FILE):
        with open(SETTINGS_FILE, 'r') as f:
            settings = json.load(f)
        return settings

settings = load_settings()
ngrok_token = settings['ngrok_token']
commandline_arguments = settings['commandline_arguments']

# ======================== TUNNEL ========================
password = "x1101"
def get_public_ip(version='ipv4'):
    try:
        url = f'https://api64.ipify.org?format=json&{version}=true'
        response = requests.get(url)
        data = response.json()
        public_ip = data['ip']
        return public_ip
    except Exception as e:
        print(f"Error getting public {version} address:", e)

public_ipv4 = get_public_ip(version='ipv4')

tunnel_class = pickle.load(open(f"{root_path}/new_tunnel", "rb"), encoding="utf-8")
tunnel_port= 1101
tunnel = tunnel_class(tunnel_port)
tunnel.add_tunnel(command="cl tunnel --url localhost:{port}", name="cl", pattern=re.compile(r"[\w-]+\.trycloudflare\.com"))
tunnel.add_tunnel(command="lt --port {port}", name="lt", pattern=re.compile(r"[\w-]+\.loca\.lt"), note="Password : " + "\033[32m" + public_ipv4 + "\033[0m" + " rerun cell if 404 error.")

# ======================== TUNNEL ========================

# fixing path...
!sed -i 's#\/home\/studio-lab-user\/content#{root_path}#g' {webui_path}/config.json

with tunnel:
    !#python -m http.server 1101
    %cd {webui_path}

    if ngrok_token:
        commandline_arguments += ' --ngrok ' + ngrok_token
    commandline_arguments += f" --port=1101 " #  --encrypt-pass={password}

    !COMMANDLINE_ARGS="{commandline_arguments}" python launch.py

    start_colab = float(open(f'{webui_path}/static/colabTimer.txt', 'r').read())
    time_since_start = str(timedelta(seconds=time.time()-start_colab)).split('.')[0]
    print(f"\n⌚️ \033[0mВы проводите эту сессию в течение - \033[33m{time_since_start}\033[0m\n\n")